## Question 7 - ResNet

In [1]:
import os
import glob
import torch
import numpy as np
from PIL import Image

from tqdm import tqdm
from collections import Counter
from xml.etree import ElementTree as ET

from torchvision import transforms, models
from torch.utils.data import Dataset, DataLoader

## Load the dataset

In [2]:
val_labels = "./data/MaskedFace/val/labels"
val_imgs = "./data/MaskedFace/val/images"

y_true = glob.glob(os.path.join(val_labels,"*.txt"))
images = glob.glob(os.path.join(val_imgs,"*.png"))

In [3]:
test_dataset = {
    'images': images,  # list of image paths
    'y_true': y_true,  # list of label paths
}

In [4]:
def count_obj(txt_file, n_class):
    with open(txt_file, 'r') as file:
        lines = file.readlines()
    # Extracting the class identifiers from each line
    class_ids = [int(line.split()[0]) for line in lines]

    # Counting the occurrences of each class
    class_counts = Counter(class_ids)

    # Sorting the dictionary by class id and converting it to a list of counts
    sorted_counts = [class_counts[i] if i in class_counts else 0 for i in range(n_class)]
    return sorted_counts

In [5]:
gt_counts = []
for idx , (img , txt) in enumerate(tqdm(zip(test_dataset['images'], test_dataset['y_true']))):
    # get ground truth
    obj_count = count_obj(txt, 3)
    gt_counts.append(obj_count)

85it [00:00, 96.70it/s] 


## Load the model

In [6]:
class ImageDataset(Dataset):
    def __init__(self, directory, transformations=None):
        self.directory = directory
        self.transformations = transformations
        self.filenames = [file for file in os.listdir(directory) if file.endswith('.png')]
        self.labels_array = np.zeros((len(self.filenames), 3), dtype=np.int64)

    def __len__(self):
        return len(self.filenames)

    def __getitem__(self, index):
        file_path = os.path.join(self.directory, self.filenames[index])
        img = Image.open(file_path).convert('RGB')
        labels = self.extract_labels(file_path.replace('.png', '.xml'))
        
        if self.transformations:
            img = self.transformations(img)
        
        self.labels_array[index] = labels
        return img, torch.tensor(labels, dtype=torch.float32)

    def extract_labels(self, xml_path):
        xml_data = ET.parse(xml_path)
        categories = {'with_mask': 0, 'without_mask': 0, 'mask_weared_incorrect': 0}
        for item in xml_data.getroot().findall('object'):
            categories[item.find('name').text] += 1
        return list(categories.values())

# Define image transformations
image_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(size=256, scale=(0.8, 1.0)),
        transforms.RandomRotation(degrees=15),
        transforms.ColorJitter(),
        transforms.RandomHorizontalFlip(),
        transforms.CenterCrop(size=224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'val': transforms.Compose([
        transforms.Resize(size=256),
        transforms.CenterCrop(size=224),
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ])
}

# Initialize the pretrained ResNet18 model and modify the fully connected layer
pretrained_model = models.resnet18(pretrained=True)
pretrained_model.fc = torch.nn.Linear(pretrained_model.fc.in_features, 3)

# Create the dataset and dataloaders
training_data = ImageDataset('data/MaskedFace/train', transformations=image_transforms['train'])
validation_data = ImageDataset('data/MaskedFace/val', transformations=image_transforms['val'])

train_data_loader = DataLoader(training_data, batch_size=32, shuffle=True)
validation_data_loader = DataLoader(validation_data, batch_size=32)

# Setup device, loss function, optimizer, and learning rate scheduler
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
pretrained_model.to(device)

D:\Anaconda3\envs\what\lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
D:\Anaconda3\envs\what\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
  

In [7]:
import copy
from sklearn.metrics import mean_absolute_error

# Setup device, loss function, optimizer, and learning rate scheduler
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
pretrained_model.to(device)

loss_function = torch.nn.MSELoss()
optimizer = torch.optim.SGD(pretrained_model.parameters(), lr=0.001, momentum=0.9)
learning_rate_scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=7, gamma=0.1)

# Function to evaluate the model's performance on validation data
def evaluate_performance(model, loader):
    model.eval()
    total_error = 0.0
    for imgs, lbls in loader:
        imgs, lbls = imgs.to(device), lbls.to(device)
        with torch.no_grad():
            predictions = model(imgs)
        error = mean_absolute_error(lbls.cpu().detach().numpy(), predictions.cpu().detach().numpy(), multioutput='raw_values')
        total_error += np.sum(error)
    return total_error / len(loader.dataset)

# Early stopping and model saving setup
best_model_wts = copy.deepcopy(pretrained_model.state_dict())
best_loss = float('inf')
early_stopping_patience = 3
patience_counter = 0

# Training loop
epochs = 10
for epoch in range(epochs):
    pretrained_model.train()
    epoch_loss = 0.0
    for imgs, lbls in tqdm(train_data_loader):
        imgs, lbls = imgs.to(device), lbls.to(device)
        optimizer.zero_grad()
        predictions = pretrained_model(imgs)
        loss = loss_function(predictions, lbls)
        loss.backward()
        optimizer.step()
        epoch_loss += loss.item()
    
    learning_rate_scheduler.step()
    
    # Validation phase
    validation_loss = evaluate_performance(pretrained_model, validation_data_loader)
    print(f'Epoch {epoch+1}, Loss: {epoch_loss / len(train_data_loader):.3f}, Validation Loss: {validation_loss:.3f}')
    
    # Check for early stopping
    if validation_loss < best_loss:
        best_loss = validation_loss
        best_model_wts = copy.deepcopy(pretrained_model.state_dict())
        torch.save(pretrained_model.state_dict(), 'best_model.pth')
        

# Load the best model weights
pretrained_model.load_state_dict(torch.load('best_model.pth'))

# Final evaluation on the validation dataset
validation_error = evaluate_performance(pretrained_model, validation_data_loader)
print(f'Validation MAE: {validation_error * 100:.2f}%')

# Print label counts from the training dataset
print(training_data.labels_array)

100%|██████████████████████████████████████████████████████████████████████████████████| 22/22 [02:28<00:00,  6.76s/it]


Epoch 1, Loss: 13.687, Validation Loss: 0.191


100%|██████████████████████████████████████████████████████████████████████████████████| 22/22 [02:12<00:00,  6.02s/it]


Epoch 2, Loss: 10.426, Validation Loss: 0.219


100%|██████████████████████████████████████████████████████████████████████████████████| 22/22 [02:18<00:00,  6.28s/it]


...

Epoch 8, Loss: 6.198, Validation Loss: 0.123


100%|██████████████████████████████████████████████████████████████████████████████████| 22/22 [02:09<00:00,  5.87s/it]


Epoch 9, Loss: 5.333, Validation Loss: 0.128


100%|██████████████████████████████████████████████████████████████████████████████████| 22/22 [02:36<00:00,  7.11s/it]


Epoch 10, Loss: 4.443, Validation Loss: 0.125
Validation MAE: 12.31%
[[1 2 0]
 [8 1 0]
 [3 0 1]
 ...
 [3 0 0]
 [1 0 0]
 [1 1 0]]


## Evaluate on the test set

In [8]:
# Function to evaluate the model's performance on validation data
def evaluate_performance(model, loader):
    model.eval()
    total_error = 0.0
    for imgs, lbls in loader:
        imgs, lbls = imgs.to(device), lbls.to(device)
        with torch.no_grad():
            predictions = model(imgs)
        error = mean_absolute_error(lbls.cpu().detach().numpy(), predictions.cpu().detach().numpy(), multioutput='raw_values')
        print(error)
        total_error += np.sum(error)
    return total_error / 3

In [9]:
# Load the best model weights
pretrained_model.load_state_dict(torch.load('best_model.pth'))

# Final evaluation on the validation dataset
validation_error = evaluate_performance(pretrained_model, validation_data_loader)
print(f'Validation MAE: {validation_error * 100:.2f}%')

[1.5965363  1.3042079  0.25560504]
[1.8177493  1.5732876  0.45420742]
[1.9562395  1.3338923  0.17067692]
Validation MAE: 348.75%


In [11]:
counts = []
for idx , (img , lbls) in enumerate(tqdm(validation_data)):
    img, lbls = img.to(device), lbls.to(device)
    with torch.no_grad():
        predictions = pretrained_model(torch.unsqueeze(img, 0))[0]
    counts.append(predictions.detach().numpy())

100%|██████████████████████████████████████████████████████████████████████████████████| 85/85 [00:11<00:00,  7.45it/s]


In [17]:
counts

[array([14.919903  ,  1.9947946 ,  0.65775687], dtype=float32),
 array([ 6.8552303 , -0.18041131,  0.07070862], dtype=float32),
 array([ 1.0139127 ,  0.2854728 , -0.08013925], dtype=float32),
 array([4.438932  , 0.7808308 , 0.05505312], dtype=float32),
 array([7.2354264 , 3.4551375 , 0.30724907], dtype=float32),
 array([5.588563  , 0.6697209 , 0.17777884], dtype=float32),
 array([ 1.150365  ,  0.6162016 , -0.10613517], dtype=float32),
 array([ 8.920831  ,  0.6018489 , -0.06503136], dtype=float32),
 array([1.95457   , 0.17450362, 0.05267046], dtype=float32),
 array([2.5774434 , 0.9776695 , 0.18825674], dtype=float32),
 array([ 2.6093178 ,  0.48708877, -0.17551954], dtype=float32),
 array([ 0.16392124,  0.5478727 , -0.19237904], dtype=float32),
 array([ 4.6288757 ,  0.1531632 , -0.03170557], dtype=float32),
 array([ 1.8586371 ,  0.6651823 , -0.02203152], dtype=float32),
 array([3.2771707 , 3.1532748 , 0.14557752], dtype=float32),
 array([3.8890243 , 2.2504125 , 0.05863352], dtype=float32

## MAPE

In [12]:
def compute_mape(prediction, truth):
    mape = np.mean( np.abs(truth - prediction) / np.maximum(truth, np.ones_like(truth)) ) * 100
    return mape

In [13]:
MAPE = compute_mape(np.array(counts), gt_counts)

In [14]:
print(MAPE)

68.38530732497205


## Final Score

In [15]:
if MAPE <= 10:
    print("Score: ", 25*1.0)
elif MAPE <= 15:
    print("Score: ", 25*0.875)
elif MAPE <= 20:
    print("Score: ", 25*0.75)
elif MAPE <= 25:
    print("Score: ", 25*0.625)
elif MAPE <= 30:
    print("Score: ", 25*0.5)
else:
    print("Score: ", 0)  

Score:  0
